# Training on Your Private Data - by NathMath @ bilibili

大家好，这里是Nathmath。我将用一个系列给你们讲解如何基于预训练好的底模进行大语言模型的私有数据微调。
> * 区别于部分UP主，我可能会“废话”很多。但是，“废话”才是你们学习的基础。因为我的“废话”是在讲解原理，让你们`能“鱼”也能“渔”`（钓鱼），意思是懂得原理，就可以不仅仅学会这一个微调，并且能够自己用在其他需要的地方，迁移学习。而不是仅仅学会我这一个东西，无法举一反三。

> * 本系列视频特别推荐大家动手。以本期视频举例，很多同学还不会准备数据集，没事，请一定要拿我的数据先跑一遍，遍跑遍听我的讲解，理解每一步在做什么；我后面的视频会继续教你们怎么准备数据集（会的同学仅看本期就可以），以及怎么进行多轮对话训练、怎么进行思考训练、怎么进行其他模型的训练；当然，最基础的，建议大家自己`先照猫画虎把我的Notebook跑通`，然后再自己尝试自己的数据。

> * 微调和训练是很难很难的内容。包括训练数据准备。在行内，有着“`数据处理80%，建模训练20%`”的行话，意思是数据处理所消耗的时间和精力占到整个机器学习的80%，其也决定了你模型的质量的80%，因为"garbage in, garbage out"（进去的是垃圾，出来的也是垃圾）。大家`一定不要灰心`，如果想学的话，踏踏实实学，有问题就问ChatGPT/DeepSeek，它能解决很多问题。

> * 关于在线训练平台。UP个人推荐Kaggle。原因是`每周`有30小时的免费的T4(16G)x2的GPU使用，需要注册并完成手机号认证(认证时候中国手机记着加上86)。另外提醒，数据特别敏感的个人或者企业用户请自己花钱租用服务器。

v20 版本更新的内容：
* 使用了冷启动，将ckpt-1418的模型导入并继续训练
* 新增了基于同内容的多轮对话生成，改善了多轮对话生成不同游戏内容的能力，防止过拟合。
* 继续训练了基于多轮对话的训练集，防止了过拟合

## 1. Prepare the Environment

In [ ]:
# Reference https://colab.research.google.com/drive/1Ys44kVvmeZtnICzWz0xgpRnrIOjZAuxp?usp=sharing#scrollTo=FqfebeAdT073
# 参考文献

* Unsloth supports Llama, Mistral, Phi-3, Gemma, Yi, DeepSeek, Qwen, TinyLlama, Vicuna, Open Hermes etc
* Unsloth supports 16bit LoRA or 4bit QLoRA. Both 2x faster.
* With [PR 26037](https://github.com/huggingface/transformers/pull/26037), we support downloading 4bit models **4x faster**! [Our repo](https://huggingface.co/unsloth) has Llama, Mistral 4bit models.

In [ ]:
# Modified Auther NathMath, open-sourced with Apache-2.0 Licence
# 修改作者：NathMath，以Apache-2.0 Licence许可证开源

In [1]:
# Use Multi-GPUs if available
# 可行时使用双CPU，适用于Kaggle T4x2

import os
os.environ["CUDA_VISIBLE_DEVICES"] = "0,1"
print("Completed")

Completed


In [3]:
# Install or import unsloth
# 安装或导入用于微调的unsloth库
if "Mute" != None:
    # 静音安装
    !pip install unsloth=="2025.3.18" > /dev/null
else:
    !pip install unsloth=="2025.3.18"

# It is slow; so be patient
# 这一步很慢请耐心等待

ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
fastai 2.7.18 requires torch<2.6,>=1.10, but you have torch 2.6.0 which is incompatible.
langchain 0.3.12 requires async-timeout<5.0.0,>=4.0.0; python_version < "3.11", but you have async-timeout 5.0.1 which is incompatible.
pylibcugraph-cu12 24.10.0 requires pylibraft-cu12==24.10.*, but you have pylibraft-cu12 25.2.0 which is incompatible.
pylibcugraph-cu12 24.10.0 requires rmm-cu12==24.10.*, but you have rmm-cu12 25.2.0 which is incompatible.
tensorflow-decision-forests 1.10.0 requires tensorflow==2.17.0, but you have tensorflow 2.17.1 which is incompatible.
torchaudio 2.5.1+cu121 requires torch==2.5.1, but you have torch 2.6.0 which is incompatible.


In [ ]:
# DO NOT CARE BUG "ERROR: pip's dependency resolver does not currently take into account"
# 这个报错不用管：“ERROR: pip's dependency resolver does not currently take into account”

In [4]:
# Import torch backend
# 导入torch后端
import torch

torch_version = torch.cuda.get_device_capability()
torch_major_v, torch_minor_v = torch_version
print(torch_major_v, torch_minor_v)
# The first version digit must be greater or equal to 7, or a bug will be raised
# 第一个数大版本必须为7或者以上，否则会提示CUDA运算版本不足bug

# If an error is thrown here, then it means you DO NOT have a valid NVIDIA accelerator
# 如果这里报错，那么意味着你没有一个有效的NVIDIA显卡作为运算加速器，请选择T4x2而不是P100，P100会提示版本不足

7 5


In [5]:
# Install other dependences
# 安装其他依赖项
if "Mute" != None:
    # 静音安装
    !pip install xformers trl peft accelerate bitsandbytes  > /dev/null
else:
    !pip install xformers trl peft accelerate bitsandbytes 

In [6]:
# Import unsloth FastLanguageModel
# 导入FastLanguageModel
from unsloth import FastLanguageModel

🦥 Unsloth: Will patch your computer to enable 2x faster free finetuning.
Unsloth: Failed to patch Gemma3ForConditionalGeneration.
🦥 Unsloth Zoo will now patch everything to make training faster!


In [7]:
# See if both GPUs are activated
# 看看是否两个GPU都被激活了

gpu_count = torch.cuda.device_count()
print("GPU Number:", gpu_count)
for i in range(gpu_count):
    print(f"GPU {i}: {torch.cuda.get_device_name(i)}")

GPU Number: 2
GPU 0: Tesla T4
GPU 1: Tesla T4


In [8]:
# Import training utilities
# 导入其他训练工具
from trl import SFTTrainer
from transformers import TrainingArguments
from unsloth import is_bfloat16_supported

In [9]:
# Import data science packeges
# 导入数据科学使用的包
import random
import numpy as np
import pandas as pd

In [10]:
# By Nathmath

## 2. Configurate the underlying model

In [11]:
# HF token
# HF 的token，如果你需要把训练好的模型保存到hugging face时需要
_global_hf_token = ""

In [12]:
# Model configuration
# 模型设定
_global_model_name = "unsloth/gemma-2-9b-bnb-4bit"    # HF 模型识别名称
_global_model_max_seqlen = 4096                       # 模型的最长输出tokens数，小说设置到8192，但显著增加训练时间
                                                      # v-20 更改到4096, 原2048
_global_model_dtype = None
_global_model_load_in_4bit = True


In [13]:
# Model training seed configuration
# 模型训练时的种子，随机生成一个，你也可以自己设定一个
_train_seed = int(np.random.rand() * 2 ** 32)
_train_seed

4127228089

## 2.1. Load the base model into the environment

In [14]:
# Load the pretrained model
# 导入HF上预训练好的底模
if False:
    _global_model, _global_tokenizer = FastLanguageModel.from_pretrained(
    model_name=_global_model_name,
    max_seq_length=_global_model_max_seqlen,
    dtype = _global_model_dtype,
    load_in_4bit = _global_model_load_in_4bit
)
else:
    _global_model, _global_tokenizer = FastLanguageModel.from_pretrained(
    model_name="DOFOFFICIAL/ThisIsNewTmp",  # Your previously saved model
    max_seq_length=_global_model_max_seqlen,
    dtype = _global_model_dtype,
    load_in_4bit = _global_model_load_in_4bit
)
# You must see Tesla T4. Num GPUs = 2. here, or you only have 1 GPU
# 在这里你必须看到GPU数量=2否则你只有1个GPU，训练会慢很多

==((====))==  Unsloth 2025.3.18: Fast Gemma2 patching. Transformers: 4.51.0.
   \\   /|    Tesla T4. Num GPUs = 2. Max memory: 14.741 GB. Platform: Linux.
O^O/ \_/ \    Torch: 2.6.0+cu124. CUDA: 7.5. CUDA Toolkit: 12.4. Triton: 3.2.0
\        /    Bfloat16 = FALSE. FA [Xformers = 0.0.29.post3. FA2 = False]
 "-____-"     Free license: http://github.com/unslothai/unsloth
Unsloth: Fast downloading is enabled - ignore downloading bars which are red colored!


model.safetensors:   0%|          | 0.00/6.13G [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/46.4k [00:00<?, ?B/s]

tokenizer.model:   0%|          | 0.00/4.24M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/636 [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/17.5M [00:00<?, ?B/s]

adapter_model.safetensors:   0%|          | 0.00/432M [00:00<?, ?B/s]

Unsloth 2025.3.18 patched 42 layers with 42 QKV layers, 42 O layers and 42 MLP layers.


## 3. Load and process the data used

In [ ]:
# Patch the model and enable LoRA adapters
# 设置模型补丁：你要怎么选择训练参数

# Only run this block when you FIRST configurate your model
# 只需要初始化一次，在最开始patch你的模型的时候跑就可以
if False:
    _global_model = FastLanguageModel.get_peft_model(
        _global_model,
        r = 32,                 # 选择任何大于0 的数，建议16或32或64，过大容易过拟合，且会很慢
        target_modules = ["q_proj", "k_proj", "v_proj", "o_proj", "gate_proj", "up_proj", "down_proj",],
        lora_alpha = 16,        # 同上，建议选择16或者32
        lora_dropout = 0,       # 建议选择0加速，或者0.1略微进行正则化防止过拟合
        bias = "none",
        use_gradient_checkpointing = "unsloth",
        random_state = _train_seed,
        use_rslora = False,     # True以开启rank stabilized LoRA，建议选False
        loftq_config = None,
        # Unsloth有LoRA adapters技术，因此不用训练整个模型，仅仅训练1~10%的层左右
    )

In [16]:
# Standard Alpaca Prompt formatting template
# 标准Alpaca提示词模板
alpaca_prompt = """{}

### Instruction:
{}

### Response:
{}

"""
alpaca_prompt_multi = """### Instruction:
{}

### Response:
{}

"""
alpaca_prompt_infer = """{}

### Instruction:
{}

### Response:
"""
# {}0: System Prompt 系统提示词
# {}1: User Prompt 用户提示词
# {}2: Assistant Response 智能助理回复

# Must add EOS_TOKEN
EOS_TOKEN = _global_tokenizer.eos_token


In [17]:
# Formatting prompts for training
def formatting_prompts(query):
    system    = query["system"]
    instructions = query["user"]
    outputs   = query["assistant"]
    texts = []
    for syst, usr, assit in zip(system, instructions, outputs):
        # Process \n\n to \n to avoid alpaca issues
        syst = syst.replace("\n\n", "\n") if syst is not None else ""
        usr = usr.replace("\n\n", "\n")
        assit = assit.replace("\n\n", "\n")

        # Must add EOS_TOKEN, otherwise your generation will go on forever!
        text = alpaca_prompt.format(syst, usr, assit) + EOS_TOKEN
        texts.append(text)
    return { "formatted" : texts, }


In [18]:
# Formatting prompts for multi-round training
def formatting_prompts_multi(query, 
                              *, 
                             m: int = 2, 
                             n: int = 12, 
                             num_conversations: int | None | float = None,
                             seed : int | None = None):
    """
    Constructs formatted text for multi-round conversations.
    Simply converted. Assume conversations are independent
    
    Parameters:
    query: dict, containing three keys "system", "user", and "assistant", corresponding to a list of single-round conversation data.
    m, n: int, specifies the interval [m, n] for randomly selecting the number of conversation rounds.
    num_conversations: The number of multi-round conversations generated, which is the same as the number of original data by default.
    seed: int | None, optional, used to set the random seed to ensure reproducibility.
    """
    system = query["system"]
    instructions = query["user"]
    outputs = query["assistant"]

    if seed is not None:
        random.seed(seed)

    total_samples = len(system)
    # If the number of generated samples is not specified, 
    # the default is to generate multiple rounds of dialogue with the same number of original samples.
    if num_conversations is None:
        num_conversations = total_samples
    elif isinstance(num_conversations, float):
        num_conversations = int(total_samples * num_conversations)

    texts = []
    for _ in range(num_conversations):
        # Randomly generate the number of rounds t included in this multi-round dialogue 
        # (not exceeding the total number of samples)
        t = random.randint(m, min(n, total_samples))
       
        # Randomly draw t samples of index (no repetition)
        indices = random.sample(range(total_samples), t)
       
        # Use the first sampled system prompt as the start of the conversation
        conv_system = system[indices[0]]
        conv_system = conv_system.replace("\n\n", "\n") if conv_system is not None else ""
        conv_text = ""
        # Traverse the extracted samples and add user input and 
        # assistant replies in sequence
        for i, idx in enumerate(indices):
            usr = instructions[idx].replace("\n\n", "\n")
            assit = outputs[idx].replace("\n\n", "\n")
            # Add user + assist conditional on whether it is the 1st or not
            if i == 0:
                conv_text += alpaca_prompt.format(conv_system, usr, assit)
            else:
                conv_text += alpaca_prompt_multi.format(usr, assit)
            # Must add EOS_TOKEN, otherwise your generation will go on forever!
            conv_text += EOS_TOKEN
            
        texts.append(conv_text)
    return {"formatted": texts, }
    

In [19]:
# Load your local dataset
# 加载你的dataset(替换成你的csv文件)
from datasets import load_dataset

# Replace this by your remote file
# 替换这个链接为你的github/huggingface数据文件，建议使用csv/parq
url = r"https://huggingface.co/DOFOFFICIAL/NathUI-Tutorial/resolve/main/dataset/TrainGemma2.gameintro.queries.v2.lf.csv"
dataset = load_dataset("csv", data_files=url, split = "train")

TrainGemma2.gameintro.queries.v2.lf.csv:   0%|          | 0.00/30.7M [00:00<?, ?B/s]

Generating train split: 0 examples [00:00, ? examples/s]

In [20]:
# See what is it like
# 看看加载的数据是否正确
dataset[495]

{'Unnamed: 0': '173_0',
 'system': '你是一个游戏剧情规划师。',
 'user': '请根据游戏名编写游戏介绍：【游戏名】：Marguerite Sphere -マーガレット スフィア-。',
 'assistant': '真要用最简洁语言来形容这城镇的话，那就是『花之街』。\n这是充满异国情调的港口城市——白美根。\n在这所到之处皆是野生雏菊的城镇里，有着一个传说。\n——在拥有纯粹专一思念的少年少女面前，花之精灵将为他们送上，能够实现愿望的雏菊之花——\n如此的白美根街住着一对双胞胎兄妹——此花大地、此花茉莉，如今他们都在私立白美根学园上学。\n妹妹成绩优秀、头脑清晰，还有着能让学校男生们都为之着迷的可爱容貌。\n可惜的是，与那容貌相对的，她却是不管对方是谁都尖酸刻薄相待的冰山利刃。\n也正是这巨大反差，让她成为了备受他人注目的存在。\n然而，其实她只是异常腼腆，以至于没能好好表现自己，着实楚楚可怜的妹妹罢了。\n这样的她和哥哥大地，就在朋友们的簇拥下过着轻松明快的每一天。\n那样的日子，想必会一直持续下去。没错，一直持续，直到今天……\n「你还真是百年难得一遇的女难相呀……」\n这些话出自于一位无意间碰到却被硬拉着占卜的占卜师之口。\n在这点缀着纯白花朵的城镇里，如梦似幻又稍稍不可思议的恋爱故事就此拉开序幕……'}

In [21]:
# Map the training data into the formatted strings
# 将你的原始数据转化为Alpaca格式化数据
if False:
    dataset_format = dataset.map(formatting_prompts, batched = True,)
else:
    # Multi-round conversation 多轮对话
    dataset_format = dataset.map(formatting_prompts_multi, batched = True)

Map:   0%|          | 0/28599 [00:00<?, ? examples/s]

In [22]:
# See what is it like again
# 看看格式化后的数据是否正确
dataset_format[495]

{'Unnamed: 0': '173_0',
 'system': '你是一个游戏剧情规划师。',
 'user': '请根据游戏名编写游戏介绍：【游戏名】：Marguerite Sphere -マーガレット スフィア-。',
 'assistant': '真要用最简洁语言来形容这城镇的话，那就是『花之街』。\n这是充满异国情调的港口城市——白美根。\n在这所到之处皆是野生雏菊的城镇里，有着一个传说。\n——在拥有纯粹专一思念的少年少女面前，花之精灵将为他们送上，能够实现愿望的雏菊之花——\n如此的白美根街住着一对双胞胎兄妹——此花大地、此花茉莉，如今他们都在私立白美根学园上学。\n妹妹成绩优秀、头脑清晰，还有着能让学校男生们都为之着迷的可爱容貌。\n可惜的是，与那容貌相对的，她却是不管对方是谁都尖酸刻薄相待的冰山利刃。\n也正是这巨大反差，让她成为了备受他人注目的存在。\n然而，其实她只是异常腼腆，以至于没能好好表现自己，着实楚楚可怜的妹妹罢了。\n这样的她和哥哥大地，就在朋友们的簇拥下过着轻松明快的每一天。\n那样的日子，想必会一直持续下去。没错，一直持续，直到今天……\n「你还真是百年难得一遇的女难相呀……」\n这些话出自于一位无意间碰到却被硬拉着占卜的占卜师之口。\n在这点缀着纯白花朵的城镇里，如梦似幻又稍稍不可思议的恋爱故事就此拉开序幕……',
 'formatted': '你是一个文字冒险游戏剧情策划师。根据我提供的数据和游戏信息，发挥你的想象力，写出一段以对白和叙事为主的游戏介绍。\n\n### Instruction:\n请根据游戏名和游戏特色编写游戏介绍：【游戏名】：牛顿与苹果树 - ニュートンと林檎の樹  Newrin，【游戏特色】：性转， 萝莉， 秋野花， 剧情， 小仓结衣， R18， 纯爱， 黄油。\n\n### Response:\n主人公 朝永修二和青梅竹马的一二三 四五为了寻找行踪不明的修二祖父，一个不留神就呼的一下穿越了。\n回过神来眼前的是仅仅一名的少女。没错，有什么好隐藏的！\n她就是后世被人敬仰那个传说中的近代科学之父，艾萨克#牛顿！\n没错，牛顿是金发贫乳美少女！！！！！！！！！！！！！！！\n不过此时的修二和四五还不知道这一切，没错知道的只有我这个天之音而已。\n于是愣头愣脑的修二，就这么在牛顿的面前，在金发贫乳美少女的表

In [23]:
# Shuffle the dataset for randomness
# 混淆重排序，为了防止过拟合
shuffled_dataset = dataset_format.shuffle(seed = 253831246211)
shuffled_dataset

Dataset({
    features: ['Unnamed: 0', 'system', 'user', 'assistant', 'formatted'],
    num_rows: 28599
})

In [24]:
# Slice the dataset to avoid entire loading that costs VRAM too much
# 对数据集进行切片，以避免整个加载耗费过多的 VRAM，如果显存爆了调用这个
if True:
    #                                                   L   R + 1   step
    sliced_dataset = shuffled_dataset.select(range(    0,   4200,    1))
    print(sliced_dataset)

Dataset({
    features: ['Unnamed: 0', 'system', 'user', 'assistant', 'formatted'],
    num_rows: 4200
})


## 4. Setup the trainer

In [25]:
# Configurate the model to train
# 设置你训练模型的训练参数
trainer = SFTTrainer(
    model = _global_model,
    tokenizer = _global_tokenizer,  
    train_dataset = sliced_dataset,        # 这是你formatted格式化后，shuffle后的数据，也可以是slice后的数据
    dataset_text_field = "formatted",      # 这个字段需要与之前format函数中新建的字段保持一致
    max_seq_length = _global_model_max_seqlen,
    dataset_num_proc = 4,                  # 建议设置为4如果你使用的是colab或者kaggle
    packing = False,
    args = TrainingArguments(
        per_device_train_batch_size = 1,   # 每一个GPU训练的batchsize，建议设置为1或2或4或8如果你使用的是colab或者kaggle
                                           # * 这是最推荐你们微调的参数，如果你的底模很大，选择更小的值；反之亦然
                                           # * 如果提示爆显存了，那么设置成更小的值（最小为1）；但是，过小的值会使得训练变慢
        gradient_accumulation_steps = 12,  # 梯度累积的步数，建议设置为4或8或12，8会使得梯度更稳定，4会防止局部鞍点，不能过高，否则梯度调整次数不够
        warmup_steps = 5,                  # · 冷启动参数，在训练开始时，学习率通常从较小的值逐渐增加到设定的初始学习率，
                                           # · 以避免训练初期模型不稳定或收敛困难的情况，定义了这一预热阶段所持续的训练步数
                                           # · 在初次训练时候应该设置更大的值，例如10或者20；微调和instruct中可以设置很小的值
        num_train_epochs = 1,              # 继续训练几个epoch，一般1足够了，如果你的数据集特别特殊且样本量较小，设为2
                                           # · 什么是epoch和step? 一个step指的是一次数据传递，一个batch包含传递了所有数据的k个steps
        learning_rate = 15e-5,             # 学习率，权重更新的速度，在微调中设置较低的值防止过拟合，不能过低，否则会陷入局部鞍点
                                           # * 这是第二推荐你们微调的参数，如果你的数据是正常数据，约有大几千或者几万个，1e-4是推荐的值
                                           # * 如果你的数据样本量很小，或者格式/语言并非常规的，可以考虑使用更大的值，但是封顶建议2e-4
                                           # * 此外，如果你的batch_size设置的较大，等效learning_rate会降低，因此也建议选更大的值
        fp16 = not is_bfloat16_supported(),
        bf16 = is_bfloat16_supported(),
        logging_steps = 1,
        optim = "adamw_8bit",
        weight_decay = 0.01,               # L2正则化，UP试了很久，不建议设置太大，否则会丢模型原始数据
        lr_scheduler_type = "linear",
        seed = _train_seed,
        output_dir = "outputs",
        report_to = "none",
        dataloader_num_workers = 4,      
        # If using multi-GPUS set these, 如果使用了多GPU，保留下面的内容否则注释掉
        dataloader_pin_memory = True,
        local_rank = -1, 
        ddp_find_unused_parameters = False,
    ),
)

Unsloth: Tokenizing ["formatted"] (num_proc=4):   0%|          | 0/4200 [00:00<?, ? examples/s]

In [45]:
# GPU Stats, code is provided by unsloth
# GPU数据，代码由unsloth提供
gpu_stats = torch.cuda.get_device_properties(0)
start_gpu_memory = round(torch.cuda.max_memory_reserved() / 1024 / 1024 / 1024, 3)
max_memory = round(gpu_stats.total_memory / 1024 / 1024 / 1024, 3)
print(f"GPU = {gpu_stats.name}. Max memory = {max_memory} GB.")
print(f"{start_gpu_memory} GB of memory reserved.")

GPU = Tesla T4. Max memory = 14.741 GB.
7.486 GB of memory reserved.


## 5. Officially train the model

In [27]:
# Call gc to clear cuda cache and release unused VRAM
# 调用自动垃圾回收机制来强制清理未使用的显存对象，减少爆显存风险

import torch
import gc

gc.collect()
torch.cuda.empty_cache()
torch.cuda.ipc_collect()

In [ ]:
## Officially train the model
## 正式开始训练你的模型，耗费时间（几十分钟到数小时）
trainer_stats = trainer.train()
print("Completed.")

# 什么时候停止？如果你的学习率太大，几十步一百步loss损失函数就到0.8/0.6这个位置了，那么
# 哪怕训练数据没用完，停！ 因为接下来的都是过拟合(最简单的理解就是只会照猫画虎，不会举一反三)，训练loss不是越低越好。
# 此时，自己测试一下，如果满意，导出保存。
# 如果不满意，调低一点learning_rate，再从头训练。
# 此外，如果你们的数据集中有大量数据重复或者高度相似，也有可能很快过拟合，请考虑数据集的问题。
#
# 你们一般不会见到欠拟合然后出大问题的情况。欠拟合就再训练：如果真遇到了，再跑一次这一行代码就可以。
# 个人建议最终停止的位置是loss函数稳定到0.8 ~ 1.4之间的某一个阶段，例如已经稳定了30steps。
# 如果你们愿意略微调整一下模型而严格防止过拟合，那么可以再1.2 ~ 1.6左右停止训练，或者增加weight_decay。

In [ ]:
# Show final training stats，code is provided by unsloth
# 训练的统计数据，代码由unsloth提供
used_memory = round(torch.cuda.max_memory_reserved() / 1024 / 1024 / 1024, 3)
used_memory_for_lora = round(used_memory - start_gpu_memory, 3)
used_percentage = round(used_memory         /max_memory*100, 3)
lora_percentage = round(used_memory_for_lora/max_memory*100, 3)
print(f"{trainer_stats.metrics['train_runtime']} seconds used for training.")
print(f"{round(trainer_stats.metrics['train_runtime']/60, 2)} minutes used for training.")
print(f"Peak reserved memory = {used_memory} GB.")
print(f"Peak reserved memory for training = {used_memory_for_lora} GB.")
print(f"Peak reserved memory % of max memory = {used_percentage} %.")
print(f"Peak reserved memory for training % of max memory = {lora_percentage} %.")

## 6. Inference Test

In [ ]:
# Reload the model, if you enter for the second time
# 重新加载模型，如果你保存了然后第二次进来
if False:
    from unsloth import FastLanguageModel

    _global_model, _global_tokenizer = FastLanguageModel.from_pretrained(
        model_name="my_gameintro_gemma9b",
        max_seq_length=_global_model_max_seqlen,
        dtype = _global_model_dtype,
        load_in_4bit = _global_model_load_in_4bit
    )


In [ ]:
# If you plan to infer rather than continue to train, call this
# 如果你希望推理而不是继续训练，调用如下这行代码，训练一定不要调
if False:
    FastLanguageModel.for_inference(_global_model)  # Enable native 2x faster inference

In [52]:
# Inference
# 推理测试
FastLanguageModel.for_inference(_global_model)
inputs = _global_tokenizer(
[
    # Use Infer when doing inference
    alpaca_prompt_infer.format(
        "你是一个游戏剧情规划师。请你根据我提供的游戏名和游戏特色规划剧情，写出一段引人入胜的游戏介绍。", # system
        "请根据游戏名编写游戏介绍：【游戏名】：在终焉的世界里寻找盛开的花。", # input
        "", # output - 留空等待AI生成
    )
], return_tensors = "pt").to("cuda")

outputs = _global_model.generate(**inputs, max_new_tokens = 256, use_cache = 2048)
_global_tokenizer.batch_decode(outputs)

['<bos>你是一个游戏剧情规划师。请你根据我提供的游戏名和游戏特色规划剧情，写出一段引人入胜的游戏介绍。\n\n### Instruction:\n请根据游戏名编写游戏介绍：【游戏名】：在终焉的世界里寻找盛开的花。\n\n### Response:\n在某个世界中，存在着一位女神。\n女神创造了万物，创造了世界。\n她创造了无数的生物，创造了广阔的土地，创造了蔚蓝的大海。\n她创造了人类，创造了动物，创造了植物。\n她创造了天空，创造了大地，创造了时间。\n她创造了世界。\n女神创造了世界，她创造了万物。\n然而，女神却无法创造出令自己满意的“智慧生命体”。\n于是，女神反复尝试着创造出智慧生命体。\n然而，创造出来的智慧生命体却无法成长，都是些只会本能地行动的傻瓜。\n女神对这些傻瓜们感到厌恶，她将他们全部贬到了广袤无边的“荒野”之地。\n在那里，智慧生命体无法生存。\n在那里，智慧生命体只能被当作牲畜对待。\n在那里，智慧生命体只能被当作愚蠢的动物对待。\n女神将这些傻瓜们贬到了荒野之地。\n然而，傻瓜们最终在荒野之地创造出了文明。\n他们创造出了国家，他们创造出了秩序。\n他们创造出了智慧。\n被贬到了荒野']

In [29]:
# Inference in stream mode
# 流式推理测试
FastLanguageModel.for_inference(_global_model)
inputs = _global_tokenizer(
[
    # Use Infer when doing inference
    alpaca_prompt_infer.format(
        "你是一个游戏剧情规划师。请你根据我提供的游戏名和游戏特色规划剧情，写出一段引人入胜的游戏介绍。", # system
        "请根据游戏名和游戏特色编写游戏介绍：【游戏名】：风陇之歌 ~Tracking the footprints of time~，【游戏特色】：奇幻， 哲学， 冒险， 宗教， 神话， 白毛。", # input
        "", # output - 留空等待AI生成
    )
], return_tensors = "pt").to("cuda")

from transformers import TextStreamer
text_streamer = TextStreamer(_global_tokenizer)
_ = _global_model.generate(**inputs, streamer = text_streamer, max_new_tokens = 2048)

<bos>你是一个游戏剧情规划师。请你根据我提供的游戏名和游戏特色规划剧情，写出一段引人入胜的游戏介绍。

### Instruction:
请根据游戏名和游戏特色编写游戏介绍：【游戏名】：风陇之歌 ~Tracking the footprints of time~，【游戏特色】：奇幻， 哲学， 冒险， 宗教， 神话， 白毛。

### Response:
《风岭之歌》是一款以“时间”为主题的纯文字冒险游戏。
在故事中，玩家将扮演一名普通的大学生，因意外事故而穿越时空，
与神秘美少女“风岭”一同，在两个时代中展开寻人寻物等一系列任务。
随着故事的推进，真相也逐渐浮出水面……

<eos>


## 7. Save the model

In [ ]:
# Save model as the native huggingface version - local
# 保存模型为原生的huggingface模型到本地
_global_model.save_pretrained("my_gameintro_gemma9b")
_global_tokenizer.save_pretrained("my_gameintro_gemma9b")

# Save the merged - locel
# 保存融合的模型(包括底模)到本地
_global_model.save_pretrained_merged("my_gameintro_gemma9b_merged", _global_tokenizer, save_method = "merged_16bit",)

In [ ]:
# Save model as the native huggingface version - hf, costs time
# 保存模型为原生的huggingface模型到hf模型站，消耗时间！请为你的运行时留足时间
_global_model.push_to_hub("DOFOFFICIAL/ThisIsNewTmp", token = "hf_...")
_global_tokenizer.push_to_hub("DOFOFFICIAL/ThisIsNewTmp", token = "hf_...") 

# Save the merged - hf, costs time
# 保存融合的模型(包括底模)到hf模型站，消耗时间！请为你的运行时留足时间
_global_model.push_to_hub_merged("DOFOFFICIAL/NathUI-Tutorial", _global_tokenizer, save_method = "merged_16bit", token = "hf_...")

In [ ]:
# Save as quanted, costs time
# 保存为量化后的模型，消耗时间！请为你的运行时留足时间

# Save to Q8_0
# 保存为量化的gguf Q8_0
# _global_model.save_pretrained_gguf("my_gameintro_gemma9b_Q8_0", _global_tokenizer, quantization_method = "q8_0")
_global_model.push_to_hub_gguf("DOFOFFICIAL/ThisIsTmp", _global_tokenizer, quantization_method = "q8_0", token = "hf_...")

# Save to Q4_K_M
# 保存为量化的gguf Q4_K_M
# _global_model.save_pretrained_gguf("my_gameintro_gemma9b_Q4_K_M", _global_tokenizer, quantization_method = "q4_K_M")
_global_model.push_to_hub_gguf("DOFOFFICIAL/ThisIsTmp", _global_tokenizer, quantization_method = "q4_K_M", token = "hf_...")


In [ ]:
# Modified Auther NathMath, open-sourced with Apache-2.0 Licence
# 修改作者：NathMath，以Apache-2.0 Licence许可证开源